In [1]:
import numpy as np
import matplotlib.pyplot as plt
import os
import time
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import torch.optim.lr_scheduler as lr_scheduler
import math
import random

MIN_LIST_LEN = 14
MAX_LIST_LEN = 14
MAX_STEPS = 512

SUCCESS_REWARD = 0.5
STEP_REWARD = -0.3
COMPARISON_ENTROPY_MULTIPLIER = -0.00
SWAP_REWARD = 1.0
INVALID_ACTION_REWARD = -10.0
LONGTERM_GAMMA = 0.99
SHORTTERM_GAMMA = 0.7

EPS_START = 0.5
EPS_END = 0.05
EPS_DECAY = 1000
LR_SCHEDULER_GAMMA = 0.95
NUM_EPISODES = 200000
EPISODES_SAVE = 1000
OUTPUT_DIR = '/home/mcwave/code/autocode/datasets/rl_sort_transformer_easy/list14_transformer4_192_gamma07_step512_v3'

# Define the vocabulary
vocab = {
    'Comparison': 0,
    'Swap': 1,
    'less': 2,
    'equal': 3,
    'more': 4,
    '0': 5,
    '1': 6,
    '2': 7,
    '3': 8,
    '4': 9,
    '5': 10,
    '6': 11,
    '7': 12,
    '8': 13,
    '9': 14,
    '10': 15,
    '11': 16,
    '12': 17,
    '13': 18,
    '14': 19,
    '15': 20,
    'len1': 21,
    'len2': 22,
    'len3': 23,
    'len4': 24,
    'len5': 25,
    'len6': 26,
    'len7': 27,
    'len8': 28,
    'len9': 29,
    'len10': 30,
    'len11': 31,
    'len12': 32,
    'len13': 33,
    'len14': 34,
    'len15': 35,
    'len16': 36,
}
inv_vocab = {v: k for k, v in vocab.items()}

def compute_entropy(N, alpha=1):
    K = 2**N
    values = np.arange(K)
    unnormalized_probs = np.exp(-alpha * values)
    Z = unnormalized_probs.sum()
    probs = unnormalized_probs / Z
    return values, -np.log2(probs)

_, int_entropy = compute_entropy(4)

def get_entropy_of_integer(x):
    x = min(15, abs(x))
    return int_entropy[x]

def compute_min_delta_entropy(comparisons):
    # Initialize the result list to store minDelta values
    min_delta = None

    # Iterate through each pair in the comparisons list
    i = len(comparisons) - 1
    xi, yi = comparisons[i]
    if i == 0:
        # For i = 0, use the first case directly
        min_delta = (xi, min(yi, yi - xi), 0)
    else:
        # For i > 0, compute all possible options and select the minimal one
        options = []

        # Simple Entropy
        simple_entropy = (xi, min(yi, yi - xi), 0)
        options.append(simple_entropy)

        # First Delta Entropy
        xi_prev, yi_prev = comparisons[i - 1]
        first_delta_entropy = (xi - xi_prev, yi - yi_prev, 0)
        options.append(first_delta_entropy)

        # Second Delta Entropy (only valid for i > 1)
        if i > 1:
            xi_prev2, yi_prev2 = comparisons[i - 2]
            second_delta_entropy = (
                (xi - xi_prev) - (xi_prev - xi_prev2),
                (yi - yi_prev) - (yi_prev - yi_prev2),
                0,
            )
            options.append(second_delta_entropy)

        # Arbitrary Position Entropy (only valid for i > 1)
        for j in range(i):
            xj, yj = comparisons[j]
            arbitrary_position_entropy = (
                xi - xj,
                yi - yj,
                min(j, i - j),
            )
            options.append(arbitrary_position_entropy)

        # Find the option with the minimal sum
        min_delta = min(options, key=lambda t: sum([get_entropy_of_integer(x) for x in t]))

    entropy = sum([get_entropy_of_integer(x) for x in min_delta])
    if len(comparisons) == 1:
        return 3 * entropy
    else:
        return entropy

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Define the environment
class SortingEnv:
    def __init__(self):
        self.max_steps = MAX_STEPS

    def reset(self):
        self.length = random.randint(MIN_LIST_LEN, MAX_LIST_LEN)
        self.list = [random.randint(1, 100) for _ in range(self.length)]
        while self.list == sorted(self.list):
            self.list = [random.randint(1, 100) for _ in range(self.length)]
        self.indices = None
        self.current_step = 0
        self.done = False
        initial_token = 'len{}'.format(self.length)
        return vocab[initial_token], self.list.copy()
    
    def get_list(self):
        return self.list
    
    def get_list_len(self):
        return len(self.list)

    def step(self, action_tokens):
        action = action_tokens[0]
        reward = -0.01  # default penalty
        response_token = None

        if action == vocab['Comparison']:
            if len(action_tokens) != 3:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            index1 = action_tokens[1] - vocab['0']
            index2 = action_tokens[2] - vocab['0']
            if index1 >= self.length or index2 >= self.length or index1 < 0 or index2 < 0:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            self.indices = (index1, index2)
            if self.list[index1] < self.list[index2]:
                response_token = vocab['less']
                reward = STEP_REWARD
            elif self.list[index1] == self.list[index2]:
                response_token = vocab['equal']
                reward = STEP_REWARD * 2
            else:
                response_token = vocab['more']
                reward = STEP_REWARD
        elif action == vocab['Swap']:
            if self.indices is None:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            index1, index2 = self.indices
            prev_list = self.list.copy()
            self.list[index1], self.list[index2] = self.list[index2], self.list[index1]
            if self.list == sorted(self.list):
                reward = SUCCESS_REWARD
                self.done = True
            #elif prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]:
            #    reward = 0.1
            elif (index1 < index2 and prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]) or \
                (index1 > index2 and prev_list[index1] < prev_list[index2] and self.list[index1] >= self.list[index2]):
                reward = SWAP_REWARD
            elif (index1 < index2 and prev_list[index1] < prev_list[index2] and self.list[index1] >= self.list[index2]) or \
                (index1 > index2 and prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]):
                reward = -SWAP_REWARD
            else:
                reward = STEP_REWARD
            self.indices = None
        else:
            reward = INVALID_ACTION_REWARD
            self.done = True

        self.current_step += 1
        if self.current_step >= self.max_steps:
            self.done = True
        return response_token, reward, self.done, self.list.copy()


Using device: cuda


In [2]:
# Positional Encoding for Transformer
class PositionalEncoding(nn.Module):
    def __init__(self, d_model, max_len=512):
        super(PositionalEncoding, self).__init__()
        self.dropout = nn.Dropout(p=0.1)

        pe = torch.zeros(max_len, d_model)  # (max_len, d_model)
        position = torch.arange(0, max_len, dtype=torch.float).unsqueeze(1)  # (max_len, 1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() *
                             (-math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)  # Even indices
        pe[:, 1::2] = torch.cos(position * div_term)  # Odd indices
        pe = pe.unsqueeze(1)  # (max_len, 1, d_model)
        self.register_buffer('pe', pe)

    def forward(self, x):
        x = x + self.pe[:x.size(0)]
        return self.dropout(x)

# Transformer Model
class TransformerModel(nn.Module):
    def __init__(self, vocab_size, d_model=192, nhead=8, num_layers=4):
        super(TransformerModel, self).__init__()
        self.model_type = 'Transformer'
        self.d_model = d_model

        self.embedding = nn.Embedding(vocab_size, d_model)
        self.pos_encoder = PositionalEncoding(d_model)
        encoder_layers = nn.TransformerEncoderLayer(d_model, nhead)
        self.transformer_encoder = nn.TransformerEncoder(encoder_layers, num_layers)
        self.decoder = nn.Linear(d_model, vocab_size)

        self.init_weights()

    def init_weights(self):
        initrange = 0.1
        nn.init.uniform_(self.embedding.weight, -initrange, initrange)
        nn.init.zeros_(self.decoder.bias)
        nn.init.uniform_(self.decoder.weight, -initrange, initrange)

    def forward(self, src):
        src = self.embedding(src) * math.sqrt(self.d_model)
        src = self.pos_encoder(src)
        output = self.transformer_encoder(src)
        output = self.decoder(output)
        return output

def decode(input_tokens, inv_vocab):
    return ' '.join([inv_vocab[x] for x in input_tokens])


def save_checkpoint(model, optimizer, episode, folder, filename):
    """
    Save the model and optimizer state to the designated filepath.

    Args:
        model (nn.Module): The model to save.
        optimizer (torch.optim.Optimizer): The optimizer whose state to save.
        episode (int): The current episode number.
        filepath (str): The path where to save the checkpoint.
    """
    filepath = os.path.join(folder, filename)
    # Ensure the directory exists
    os.makedirs(os.path.dirname(filepath), exist_ok=True)
    # Save the checkpoint
    torch.save({
        'episode': episode,
        'model_state_dict': model.state_dict(),
        'optimizer_state_dict': optimizer.state_dict(),
    }, filepath)
    print(f"Checkpoint saved at episode {episode} to {filepath}")

def load_checkpoint(filepath, model, optimizer):
    """
    Load the model and optimizer state from the designated filepath.

    Args:
        filepath (str): The path from where to load the checkpoint.
        model (nn.Module): The model into which to load the state_dict.
        optimizer (torch.optim.Optimizer): The optimizer into which to load the state.

    Returns:
        int: The episode number to resume from.
    """
    if os.path.isfile(filepath):
        checkpoint = torch.load(filepath, map_location=device)
        model.load_state_dict(checkpoint['model_state_dict'])
        optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        episode = checkpoint['episode']
        print(f"Checkpoint loaded from {filepath}, resuming from episode {episode}")
        return episode
    else:
        print(f"No checkpoint found at {filepath}, starting from scratch.")
        return 0

In [3]:
def compute_bellman_returns(raw_rewards, gamma):
    bellman_returns = []
    R = 0
    for r in raw_rewards[::-1]:
        R = r + gamma * R
        bellman_returns.insert(0, R)
    return bellman_returns

# Training Loop
def train(verbose=False):
    # Removed torch.autograd.set_detect_anomaly(True)
    vocab_size = len(vocab)
    model = TransformerModel(vocab_size).to(device)
    optimizer = optim.Adam(model.parameters(), lr=1e-4)  # Reduced learning rate
    scheduler = lr_scheduler.ExponentialLR(optimizer, gamma=LR_SCHEDULER_GAMMA)
    
    # Optionally, load a checkpoint
    #checkpoint_path = os.path.join(OUTPUT_DIR, "ckpt_99000_0.9940_86.73.pth")
    #load_checkpoint(checkpoint_path, model, optimizer)

    episode_cnt = 0
    total_reward = 0.0
    num_successes = 0
    total_steps = 0
    
    for episode in range(NUM_EPISODES):
        t1 = time.time()
        model.train()  # Set model to training mode
        env = SortingEnv()
        initial_token_id, current_list = env.reset()
        input_tokens = [initial_token_id]
        log_probs = []
        rewards = []
        comparisons = []
        
        state = 'expect_action'
        done = False
        success = False

        while not done and len(input_tokens) < env.max_steps:
            if verbose:
                print(decode(input_tokens, inv_vocab))
                print(env.get_list())
                print(comparisons)
            # Prepare input tensor
            input_seq = torch.tensor(input_tokens, dtype=torch.long, device=device).unsqueeze(1)  # (seq_len, batch_size)
            # Get model output
            with torch.autocast(device_type=device.type, dtype=torch.bfloat16):
                output = model(input_seq)  # (seq_len, batch_size, vocab_size)
                # Get logits for the last token
                logits = output[-1, 0, :]  # (vocab_size)

                # Check for NaNs in logits
                if torch.isnan(logits).any():
                    print(f"Episode {episode}, NaNs in logits before masking.")
                    break

                # Get valid tokens based on state
                def get_valid_tokens(state):
                    action_tokens = [vocab['Comparison'], vocab['Swap']]
                    index_tokens = [vocab[str(i)] for i in range(env.length)]
                    if state == 'expect_action':
                        return action_tokens
                    elif state == 'expect_index1':
                        return index_tokens[:-1]
                    elif state == 'expect_index2':
                        return [x for x in index_tokens if x > input_tokens[-1]]
                    else:
                        # Handle unexpected states by defaulting to expect_action
                        return action_tokens

                valid_token_ids = get_valid_tokens(state)

                # Ensure valid_token_ids are within the vocab range
                if any(idx >= vocab_size or idx < 0 for idx in valid_token_ids):
                    print(f"Episode {episode}, invalid indices in valid_token_ids: {valid_token_ids}")
                    break

                # Mask invalid tokens
                mask_value = -1e9  # Use a large negative value instead of -inf
                mask = torch.full_like(logits, mask_value).to(device)
                mask[valid_token_ids] = 0
                masked_logits = logits + mask

                # Sample action. Have some chance to randomly pick a valid action.
                eps_threshold = EPS_END + (EPS_START - EPS_END) * np.exp(-1.0 * episode / EPS_DECAY)
                if random.random() < eps_threshold:
                    masked_logits = masked_logits / 4

                # Check for NaNs in masked_logits
                if torch.isnan(masked_logits).any():
                    print(f"Episode {episode}, NaNs in masked_logits after masking.")
                    break

                # Compute probabilities
                probs = F.softmax(masked_logits, dim=0)

                # Check for NaNs in probs
                if torch.isnan(probs).any():
                    print(f"Episode {episode}, NaNs in probs after softmax.")
                    break

                try:
                    m = torch.distributions.Categorical(probs)
                    action_token = m.sample()
                    log_prob = m.log_prob(action_token)
                except ValueError as e:
                    print(f"Episode {episode}, error in sampling action: {e}")
                    break

            log_probs.append(log_prob)
            input_tokens.append(action_token.item())

            action = action_token.item()
            reward = 0.0
            if state == 'expect_action':
                if action == vocab['Comparison']:
                    state = 'expect_index1'
                elif action == vocab['Swap']:
                    if env.indices is None:
                        reward = INVALID_ACTION_REWARD
                        rewards.append(reward)
                        done = True
                        continue
                    action_tokens = [vocab['Swap']]
                    response_token, reward, done, current_list = env.step(action_tokens)
                    if done and reward == SUCCESS_REWARD:
                        success = True
                        if episode % 100 == 0:
                            print(decode(input_tokens, inv_vocab))
                    if verbose:
                        print("Reward:", reward)
                    state = 'expect_action'
                else:
                    reward = INVALID_ACTION_REWARD
                    done = True
            elif state == 'expect_index1':
                index1_token = action_token
                state = 'expect_index2'
            elif state == 'expect_index2':
                index2_token = action_token
                action_tokens = [vocab['Comparison'], index1_token.item(), index2_token.item()]
                comparisons.append((int(inv_vocab[index1_token.item()]), 
                                    int(inv_vocab[index2_token.item()])))
                response_token, reward, done, current_list = env.step(action_tokens)
                if done and reward == SUCCESS_REWARD:
                    success = True
                    if episode % 100 == 0:
                        print(1, decode(input_tokens, inv_vocab))
                else:
                    reward += COMPARISON_ENTROPY_MULTIPLIER * compute_min_delta_entropy(comparisons)
                if verbose:
                    print("Reward:", reward)
                if response_token is not None:
                    input_tokens.append(response_token)
                state = 'expect_action'
            else:
                reward = INVALID_ACTION_REWARD
                done = True

            rewards.append(reward)
        #
        success_rewards = [0.0] * len(rewards)
        if success: 
            num_successes += 1
            success_rewards[-1] = SUCCESS_REWARD

        # Save checkpoint
        if episode > 0 and episode % EPISODES_SAVE == 0:
            avg_reward = total_reward / episode_cnt
            success_rate = num_successes / episode_cnt
            avg_steps = total_steps / episode_cnt
            episode_cnt = 0
            total_reward = 0.0
            num_successes = 0
            total_steps = 0
            save_checkpoint(model, optimizer, episode, OUTPUT_DIR, f"ckpt_{episode}_{success_rate:.4f}_{avg_steps:.2f}.pth")
            #
            # Reduce the lr
            scheduler.step()
            # Optionally, log the learning rate
            current_lr = scheduler.get_last_lr()[0]
            print(f"Learning rate = {current_lr:.6f}")
        #
        assert len(log_probs) == len(rewards), "log_probs and returns have different sizes!"

        if len(log_probs) == 0:
            continue  # Skip if no actions were taken

        # Compute returns and loss within autocast
        with torch.autocast(device_type=device.type, dtype=torch.bfloat16):
            # Compute returns
            returns1 = compute_bellman_returns(rewards, SHORTTERM_GAMMA)
            returns2 = compute_bellman_returns(success_rewards, LONGTERM_GAMMA)
            returns = torch.tensor(np.array(returns1) + np.array(returns2)).to(device)

            # Check for NaNs in returns
            if torch.isnan(returns).any():
                print(f"Episode {episode}, NaNs in returns.")
                continue

            # Compute loss
            loss = 0
            for log_prob, R in zip(log_probs, returns):
                loss -= log_prob * R

            # Check for NaNs in loss
            if torch.isnan(loss):
                print(f"Episode {episode}, NaN in loss.")
                continue

        optimizer.zero_grad()
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)  # Gradient clipping
        optimizer.step()

        episode_cnt += 1
        total_reward += sum(rewards)
        total_steps += len(rewards)
        t2 = time.time()
        if episode % 1 == 0:
            print(f"Episode {episode}, loss:{loss.item():.4f}, {'succeed' if success else 'fail'}, steps:{len(rewards)}, total reward:{sum(rewards):.4f}, {t2-t1} sec")

if __name__ == "__main__":
    train(verbose=False)


/home/mcwave/.local/lib/python3.10/site-packages/torch/nn/modules/transformer.py:282: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(f"enable_nested_tensor is True, but self.use_nested_tensor is False because {why_not_sparsity_fast_path}")


Episode 0, loss:-10.4369, fail, steps:1, total reward:-10.0000, 0.3546288013458252 sec
Episode 1, loss:-43.6803, fail, steps:25, total reward:-13.1000, 0.08630776405334473 sec
Episode 2, loss:-81.1889, fail, steps:36, total reward:-13.3000, 0.09507894515991211 sec
Episode 3, loss:-15.8641, fail, steps:1, total reward:-10.0000, 0.0046002864837646484 sec
Episode 4, loss:-144.1239, fail, steps:386, total reward:-31.8000, 1.3872759342193604 sec
Episode 5, loss:-177.5649, fail, steps:275, total reward:-36.1000, 0.8053064346313477 sec
Episode 6, loss:-155.5223, fail, steps:387, total reward:-34.2000, 1.1299631595611572 sec
Episode 7, loss:-55.6246, fail, steps:11, total reward:-9.9000, 0.07727336883544922 sec
Episode 8, loss:-156.7716, fail, steps:387, total reward:-32.4000, 1.047001838684082 sec
Episode 9, loss:-154.3039, fail, steps:386, total reward:-32.5000, 1.1200568675994873 sec
Episode 10, loss:-147.7024, fail, steps:182, total reward:-28.0000, 0.5597286224365234 sec
Episode 11, loss:

Episode 91, loss:-103.5595, fail, steps:390, total reward:-15.3000, 1.1973843574523926 sec
Episode 92, loss:-60.2062, fail, steps:85, total reward:-8.8000, 0.3091285228729248 sec
Episode 93, loss:-5.1296, succeed, steps:364, total reward:-4.8000, 1.0730257034301758 sec
Episode 94, loss:-91.5431, fail, steps:390, total reward:-12.3000, 1.1462278366088867 sec
Episode 95, loss:-110.3933, fail, steps:389, total reward:-16.6000, 1.1724162101745605 sec
Episode 96, loss:-79.1213, fail, steps:171, total reward:-7.0000, 0.5490562915802002 sec
Episode 97, loss:-70.3296, fail, steps:392, total reward:-6.0000, 1.1269304752349854 sec
Episode 98, loss:-93.4819, fail, steps:392, total reward:-8.6000, 1.1752221584320068 sec
Episode 99, loss:-46.7818, fail, steps:152, total reward:-0.9000, 0.4912536144256592 sec
Episode 100, loss:-114.4379, fail, steps:245, total reward:-15.8000, 0.7090823650360107 sec
Episode 101, loss:-138.2560, fail, steps:388, total reward:-23.5000, 1.1659576892852783 sec
Episode 1

Episode 182, loss:-62.8078, fail, steps:391, total reward:-5.0000, 1.0770254135131836 sec
Episode 183, loss:-70.3434, fail, steps:391, total reward:-7.7000, 1.147554636001587 sec
Episode 184, loss:-96.0449, fail, steps:390, total reward:-14.6000, 1.1645689010620117 sec
Episode 185, loss:-51.5398, fail, steps:394, total reward:2.0000, 1.2397103309631348 sec
Episode 186, loss:-62.5091, fail, steps:392, total reward:-4.0000, 1.2020957469940186 sec
Episode 187, loss:-40.3350, fail, steps:1, total reward:-10.0000, 0.05087447166442871 sec
Episode 188, loss:8.3115, succeed, steps:350, total reward:-1.5000, 0.9295835494995117 sec
Episode 189, loss:-76.8131, fail, steps:78, total reward:-8.9000, 0.24318790435791016 sec
Episode 190, loss:-70.0118, fail, steps:393, total reward:-3.5000, 1.0808119773864746 sec
Episode 191, loss:-85.1284, fail, steps:173, total reward:-8.4000, 0.5272440910339355 sec
Episode 192, loss:-61.7082, fail, steps:392, total reward:-2.7000, 1.119678020477295 sec
Episode 193

Episode 273, loss:-43.1788, fail, steps:393, total reward:3.6000, 1.2569224834442139 sec
Episode 274, loss:-59.6250, fail, steps:163, total reward:-3.1000, 0.5329287052154541 sec
Episode 275, loss:-65.6768, fail, steps:391, total reward:-7.6000, 1.1255357265472412 sec
Episode 276, loss:-59.1076, fail, steps:391, total reward:-8.5000, 1.1714725494384766 sec
Episode 277, loss:-80.4804, fail, steps:390, total reward:-13.3000, 1.1807796955108643 sec
Episode 278, loss:-54.3850, fail, steps:392, total reward:-3.2000, 1.2019550800323486 sec
Episode 279, loss:-91.4042, fail, steps:390, total reward:-12.6000, 1.2473504543304443 sec
Episode 280, loss:-63.4521, fail, steps:392, total reward:-7.9000, 1.2079155445098877 sec
Episode 281, loss:-60.7980, fail, steps:392, total reward:-4.0000, 1.20542311668396 sec
Episode 282, loss:-61.4285, fail, steps:391, total reward:-7.6000, 1.211318016052246 sec
Episode 283, loss:-61.3597, fail, steps:391, total reward:-5.9000, 1.2068383693695068 sec
Episode 284,

...

Episode 71905, loss:2.0051, succeed, steps:224, total reward:22.2000, 0.6738944053649902 sec
Episode 71906, loss:-11.5195, fail, steps:395, total reward:10.1000, 1.1484925746917725 sec
Episode 71907, loss:1.8274, succeed, steps:230, total reward:13.5000, 0.7120084762573242 sec
Episode 71908, loss:3.4122, succeed, steps:309, total reward:22.6000, 0.909982442855835 sec
Episode 71909, loss:-7.7783, fail, steps:396, total reward:13.0000, 1.2103803157806396 sec
Episode 71910, loss:2.3461, succeed, steps:304, total reward:15.5000, 0.929915189743042 sec
Episode 71911, loss:-9.5202, fail, steps:396, total reward:13.2000, 1.1729249954223633 sec
Episode 71912, loss:3.2256, succeed, steps:375, total reward:8.2000, 1.1458840370178223 sec
Episode 71913, loss:-14.0908, fail, steps:393, total reward:-2.5000, 1.1887602806091309 sec
Episode 71914, loss:1.9843, succeed, steps:249, total reward:7.3000, 0.7839269638061523 sec
Episode 71915, loss:2.5492, succeed, steps:335, total reward:16.5000, 1.04951906

Episode 71995, loss:6.2085, succeed, steps:284, total reward:22.5000, 0.8840897083282471 sec
Episode 71996, loss:2.4379, succeed, steps:202, total reward:16.7000, 0.6254799365997314 sec
Episode 71997, loss:-4.6520, fail, steps:395, total reward:6.9000, 1.1461806297302246 sec
Episode 71998, loss:-1.2636, succeed, steps:372, total reward:18.4000, 1.1247494220733643 sec
Episode 71999, loss:0.2344, succeed, steps:238, total reward:11.9000, 0.7395844459533691 sec
len14 Comparison 6 7 more Swap Comparison 7 8 less Comparison 8 9 more Swap Comparison 9 10 more Swap Comparison 10 11 more Swap Comparison 11 12 more Swap Comparison 5 6 more Swap Comparison 4 5 more Swap Comparison 3 4 more Swap Comparison 12 13 more Swap Comparison 2 3 more Swap Comparison 0 2 more Swap Comparison 6 7 more Swap Comparison 7 8 more Swap Comparison 8 9 more Swap Comparison 9 10 more Swap Comparison 5 6 more Swap Comparison 10 11 more Swap Comparison 11 12 more Swap Comparison 4 5 less Comparison 3 4 more Swap Comp

Episode 72057, loss:-11.7792, fail, steps:394, total reward:0.7000, 1.1775083541870117 sec
Episode 72058, loss:3.4739, succeed, steps:255, total reward:23.5000, 0.7991881370544434 sec
Episode 72059, loss:-5.7757, fail, steps:394, total reward:2.5000, 1.1650655269622803 sec
Episode 72060, loss:2.6219, succeed, steps:282, total reward:10.6000, 0.8725810050964355 sec
Episode 72061, loss:1.0569, succeed, steps:222, total reward:13.6000, 0.6905612945556641 sec
Episode 72062, loss:2.2241, succeed, steps:229, total reward:20.6000, 0.6824860572814941 sec
Episode 72063, loss:3.6027, succeed, steps:315, total reward:17.2000, 0.9667766094207764 sec
Episode 72064, loss:-3.6681, fail, steps:397, total reward:16.3000, 1.1704564094543457 sec
Episode 72065, loss:1.3248, succeed, steps:222, total reward:7.0000, 0.6943554878234863 sec
Episode 72066, loss:0.5213, succeed, steps:266, total reward:9.3000, 0.78924560546875 sec
Episode 72067, loss:6.1451, succeed, steps:389, total reward:9.0000, 1.1367647647

Episode 72147, loss:4.6061, succeed, steps:273, total reward:16.6000, 1.4982450008392334 sec
Episode 72148, loss:3.8762, succeed, steps:326, total reward:24.9000, 1.7824015617370605 sec
Episode 72149, loss:-4.4297, fail, steps:398, total reward:23.1000, 2.135786771774292 sec
Episode 72150, loss:-8.1137, fail, steps:396, total reward:13.2000, 2.203390121459961 sec
Episode 72151, loss:3.0445, succeed, steps:198, total reward:19.0000, 1.1091656684875488 sec
Episode 72152, loss:-6.5765, fail, steps:395, total reward:10.3000, 2.1000900268554688 sec
Episode 72153, loss:1.3563, succeed, steps:227, total reward:10.2000, 1.2580478191375732 sec
Episode 72154, loss:9.7002, succeed, steps:373, total reward:29.3000, 1.9870264530181885 sec
Episode 72155, loss:-6.5672, fail, steps:396, total reward:11.8000, 2.148134708404541 sec
Episode 72156, loss:2.8750, succeed, steps:213, total reward:14.2000, 1.1940579414367676 sec
Episode 72157, loss:3.8004, succeed, steps:269, total reward:14.4000, 1.492188453

KeyboardInterrupt: 